In [1]:
import numpy as np
import pandas as pd
import astropy.io.fits as fits
import astropy.units as u
from astropy.cosmology import FlatLambdaCDM
import matplotlib.pyplot as plt
from sklearn.decomposition import KernelPCA
from sklearn.preprocessing import StandardScaler
import umap
import plotly.express as px

# コスモロジーモデルの設定
cosmo = FlatLambdaCDM(H0=70, Om0=0.3)

# FITSファイルのパス
fits_file_path = 'COSMOS2020_CLASSIC_R1_v2.2_p3.fits'

# フィルタリング用のカラムリスト
column = ['ez_z_phot', 'ez_z_phot_risk', 'GALEX_FUV_FLUX', 'GALEX_NUV_FLUX', 'CFHT_u_FLUX_AUTO', 'CFHT_ustar_FLUX_AUTO', 'ACS_F814W_FLUX', 'HSC_g_FLUX_AUTO', 'HSC_r_FLUX_AUTO', 'HSC_i_FLUX_AUTO', 'HSC_z_FLUX_AUTO', 'HSC_y_FLUX_AUTO', 'SC_B_FLUX_AUTO', 'SC_gp_FLUX_AUTO', 
    'SC_V_FLUX_AUTO', 'SC_rp_FLUX_AUTO', 
    'SC_ip_FLUX_AUTO', 'SC_zp_FLUX_AUTO', 
    'SC_zpp_FLUX_AUTO', 'SC_IB427_FLUX_AUTO', 
    'SC_IB464_FLUX_AUTO', 'SC_IA484_FLUX_AUTO', 
    'SC_IB505_FLUX_AUTO', 'SC_IA527_FLUX_AUTO', 
    'SC_IB574_FLUX_AUTO', 'SC_IA624_FLUX_AUTO', 
    'SC_IA679_FLUX_AUTO', 'SC_IB709_FLUX_AUTO', 
    'SC_IA738_FLUX_AUTO', 'SC_IA767_FLUX_AUTO', 
    'SC_IB827_FLUX_AUTO', 'SC_NB711_FLUX_AUTO', 
    'SC_NB816_FLUX_AUTO', 'UVISTA_Y_FLUX_AUTO', 'UVISTA_J_FLUX_AUTO', 'UVISTA_H_FLUX_AUTO', 'UVISTA_Ks_FLUX_AUTO', 'UVISTA_NB118_FLUX_AUTO', 'SPLASH_CH1_FLUX', 'SPLASH_CH2_FLUX', 'SPLASH_CH3_FLUX', 'SPLASH_CH4_FLUX']

# FITSファイルを開く
with fits.open(fits_file_path) as hdul:
    data = hdul[1].data
    
    # データをPandas DataFrameに変換
    df = pd.DataFrame(data)
    
    # フィルタリングと前処理
    df = df[df['ez_z_phot'] <= 2]
    df = df.dropna(subset=column)
    df = df[df['ez_z_phot_risk'] < 0.5]
    df = df.sort_values(by='ez_z_phot')

# 光度距離を計算して追加
df['d_L'] = df['ez_z_phot'].apply(lambda z: cosmo.luminosity_distance(z).to(u.cm).value)

# フラックス密度（μJy）から光度を計算（erg/s/Hzに変換）
for col in df.columns:
    if '_FLUX' in col:
        df[col + '_LUMINOSITY'] = 4 * np.pi * (df['d_L']**2) * df[col] * 1e-29  # μJyからerg/s/Hzに変換



# NumPyファイルに保存
# numpy_file_path = 'filtered_data.npy'
# np.save(numpy_file_path, df.to_numpy())

# print(f'フィルタリングされたデータをNumPyファイルに保存しました: {numpy_file_path}')

/home/ryuseikano/anaconda3/envs/umap/lib/python3.9/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
/tmp/ipykernel_3849600/956192061.py:50: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[col + '_LUMINOSITY'] = 4 * np.pi * (df['d_L']**2) * df[col] * 1e-29  # μJyからerg/s/Hzに変換
/tmp/ipykernel_3849600/956192061.py:50: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  d

In [7]:
  # 赤方偏移ごとに処理
for z in np.arange(0, 2.1, 0.1):
    z_min = z
    z_max = z + 0.1
    df_subset = df[(df['ez_z_phot'] >= z_min) & (df['ez_z_phot'] < z_max)]
    
    # Q1 = df_subset['ez_sfr'].quantile(0.25)
    # Q3 = df_subset['ez_sfr'].quantile(0.75)

    # カラーバーの最大値と最小値を設定
    color_max = df_subset['ez_sfr'].sort_values(ascending=False).iloc[3]
    color_min = df_subset['ez_sfr'].min()
    
    if df_subset.empty:
        continue

    # KernelPCAの適用
    X = df_subset[[col + '_LUMINOSITY' for col in column if '_FLUX' in col]]
    scaler = StandardScaler()
    X_scaled = scaler.fit_transform(X)
    
    # UMAPの適用
    umap_model = umap.UMAP(n_components=3, random_state=42)
    X_umap = umap_model.fit_transform(X_scaled)
    
    fig = px.scatter_3d(
        x=X_umap[:, 0],
        y=X_umap[:, 1],
        z=X_umap[:, 2],
        color=df_subset['ez_sfr'],
        range_color=[color_min, color_max],
        labels={'x': 'UMAP Component 1', 'y': 'UMAP Component 2', 'z': 'UMAP Component 3', 'color': 'ez_sfr'},
        title=f'UMAP for z={z_min:.1f} to z={z_max:.1f}'
    )
    fig.update_traces(marker=dict(size=1))
    fig.show()


IndexError: single positional indexer is out-of-bounds